In [34]:
import easyocr
import cv2
import matplotlib.pyplot as plt
from icecream import ic
import os
import random
from moviepy.editor import VideoFileClip

In [14]:
def get_ocr_results(image_path):
    reader = easyocr.Reader(['en']) # this needs to run only once to load the model into memory
    result = reader.readtext(image_path)
    return result

In [15]:
def get_coordinates_for_text(data, target_text):
    matching_coordinates = []

    for item in data:
        coordinates, ocr_text, _ = item  # We ignore the confidence score here
        if target_text.lower() in ocr_text.lower() :  # Case-insensitive comparison
            matching_coordinates.append(coordinates)

    return matching_coordinates

In [49]:
def generate_video(input_video_path, output_video_path, top_left_coordinate, bottom_right_coordinate,band_color):
    """
    Draws a solid rectangle on a video with error handling.

    Parameters:
    - input_video_path: Path to the input video file.
    - output_video_path: Path where the output video will be saved.
    - top_left_coordinate: Tuple (x, y) for the top left coordinate of the rectangle.
    - bottom_right_coordinate: Tuple (x, y) for the bottom right coordinate of the rectangle.
    """
    try:
        # Attempt to open the input video
        cap = cv2.VideoCapture(input_video_path)
        if not cap.isOpened():
            raise IOError(f"Could not open video file: {input_video_path}")

        # Get the video properties
        frame_width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
        frame_height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
        fps = cap.get(cv2.CAP_PROP_FPS)

        # Generate output video path by appending '_output' before the file extension
        # base_name= os.path.basename(input_video_path)
        output_video_path = f"{output_video_path}.mp4"
        ic(output_video_path)

        # Define the codec and create a VideoWriter object
        out = cv2.VideoWriter(output_video_path, cv2.VideoWriter_fourcc(*'mp4v'), fps, (frame_width, frame_height))

        frame_count = 0  # To count the number of frames processed


        # Watermark
        text = "animated_home_solutions"
        font_scale=1
        alpha=0.5
        # Prepare text properties
        font = cv2.FONT_HERSHEY_SIMPLEX
        font_thickness = 2
        text_size = cv2.getTextSize(text, font, font_scale, font_thickness)[0]
        
        # Random initial position
        text_x = random.randint(0, frame_width - text_size[0])
        text_y = random.randint(0, frame_height - text_size[1])
        
        # Random direction
        direction_x = random.choice([-1, 1])
        direction_y = random.choice([-1, 1])
        step = 5  # Speed of the movement

        while True:
            ret, frame = cap.read()
            if not ret:
                break
            
            # Watermark
            
            # Create a transparent overlay for the watermark
            overlay = frame.copy()
            
            # Add text moving across the frame
            cv2.putText(overlay, text, (text_x, text_y), font, font_scale, (255, 255, 255), font_thickness)
            cv2.addWeighted(overlay, alpha, frame, 1 - alpha, 0, frame)
            
            # Update the position of the text for the next frame
            text_x += step * direction_x
            text_y += step * direction_y

            # Bounce off the edges
            if text_x + text_size[0] > frame_width or text_x < 0:
                direction_x *= -1
            if text_y + text_size[1] > frame_height or text_y < 0:
                direction_y *= -1
            
            # Watermark END

            # Draw a solid rectangle on the frame
            cv2.rectangle(frame, top_left_coordinate, bottom_right_coordinate, band_color, -1)

            # Write the frame into the file
            out.write(frame)
            frame_count += 1
        
      
        print(f"Processed {frame_count} frames.")
    except IOError as e:
        print(f"IOError: {e}")
    except Exception as e:
        print(f"An unexpected error occurred: {e}")
    finally:
        # Release resources in the finally block to ensure they are always executed
        if 'cap' in locals() and cap.isOpened():
            cap.release()
        if 'out' in locals():
            out.release()

In [45]:
def add_audio(original_video_path, edited_video_path, output_video_path):
    """
    Adds the audio from the original video to the edited video.

    Parameters:
    - original_video_path: Path to the original video file.
    - edited_video_path: Path to the edited video file without audio.
    - output_video_path: Path where the output video with audio will be saved.
    """
    try:
        # Load the original and edited videos
        original_video = VideoFileClip(original_video_path)
        edited_video = VideoFileClip(edited_video_path)

        # Combine the audio from the original video with the edited video
        final_video = edited_video.set_audio(original_video.audio)

        # Write the output video file
        final_video.write_videofile(output_video_path, codec="libx264", audio_codec="aac")
        
        print(f"Successfully added audio to {output_video_path}")
    except Exception as e:
        print(f"Error adding audio to video: {e}")


In [17]:
def get_mid_frame(video_path,output_path = '',save_path=False):
    # Read the Video (Change the filename as per your file)
    cap = cv2.VideoCapture(video_path)

    # Get the total number of frames
    length = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    half_point = length//2 # Approximately half if number of frames are odd

    # Set the reader to the given frame number (half_point)
    cap.set(cv2.CAP_PROP_POS_FRAMES, half_point)

    # Read the frame
    ret, frame = cap.read()

    base_name = os.path.basename(video_path)
    print(base_name)
    if save_path: cv2.imwrite(f"{output_path}{base_name}_mid.png", frame)

    # Release the file pointer
    cap.release()
    return frame
# mid_frame = get_mid_frame(os.path.join('downloads','10_Parents Built a Beautiful Bedroom For Son & Daughter  3d Animation By The Stories Time  shorts.mp4'),output_path='',save_path=True)
# mid_frame = get_mid_frame('test.mp4',output_path='mid_frames/',save_path=True)
# mid_frame

### Actual code

In [27]:
mid_frame = get_mid_frame(r'test.mp4',output_path='mid_frames/',save_path=True)

test.mp4


In [28]:
ocr_results = get_ocr_results(mid_frame)
ocr_results

Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.


[([[61, 55], [109, 55], [109, 69], [61, 69]], 'BEST', 0.9950381817750114),
 ([[28, 64], [136, 64], [136, 88], [28, 88]], 'INDIAN', 0.9313570263730901),
 ([[46, 86], [78, 86], [78, 94], [46, 94]], 'ILNE', 0.12265399098396301),
 ([[81, 83], [135, 83], [135, 97], [81, 97]], 'QAMINO', 0.46622896014818577),
 ([[47, 95], [119, 95], [119, 107], [47, 107]],
  'PLAIDEM',
  0.09117240543804958),
 ([[262, 1058], [462, 1058], [462, 1088], [262, 1088]],
  'The Stories Time',
  0.9996257111612783)]

In [30]:
matches = get_coordinates_for_text(ocr_results,'stories')
matches

[[[262, 1058], [462, 1058], [462, 1088], [262, 1088]]]

In [51]:
def get_mid_band_color(image,top_left):
    color = (image[top_left[1],top_left[0]])
    blue,green,red = int(color[0]),int(color[1]),int(color[2])
    ic(color)
    return blue,green,red

band_color = get_mid_band_color(mid_frame,[262, 1058])

ic| color: array([137, 165, 190], dtype=uint8)


In [32]:
top_left = matches[0][0]
ic(top_left)
bottom_right = matches[0][2]

top_left[1]-=15
bottom_right[1]+=15
ic(top_left)

ic| top_left: [262, 1058]
ic| top_left: [262, 1043]


[262, 1043]

In [44]:
generate_video('test.mp4','stage1/test_output',top_left_coordinate=top_left,bottom_right_coordinate=bottom_right,band_color = [ 70,  80, 118])

ic| output_video_path: 'stage1/test_output.mp4'


Processed 1318 frames.


## Loop

In [24]:
filenames = next(os.walk('downloads'), (None, None, []))[2]  

In [25]:
filenames_s = sorted(filenames, key=lambda x: int(x.split('_')[0]))

In [55]:
for raw_name in list(reversed(filenames_s)):
    v_name = raw_name.split('3d')[0].strip()+' 3D home redesign animations'+'_stage1'
    filepath = os.path.join('downloads',raw_name)
    ic(filepath)
    ic(v_name)
    mid_frame = get_mid_frame(filepath,output_path='mid_frames/',save_path=True)
    ocr_results = get_ocr_results(mid_frame)
    matches = get_coordinates_for_text(ocr_results,'stories')
    top_left = matches[0][0]
    bottom_right = matches[0][2]
    band_color = get_mid_band_color(mid_frame,top_left)
    # top_left[1]-=15
    # bottom_right[1]+=15
    generate_video(filepath,'stage1/'+v_name,top_left_coordinate=top_left,bottom_right_coordinate=bottom_right,band_color = band_color)
    add_audio(filepath,'stage1/'+v_name+'.mp4','stage2/'+v_name+'.mp4')


ic| filepath: 'downloads\\74_Turn a Simple Room Into a Luxury Room in 3d Animation shorts.mp4'
ic| v_name: '74_Turn a Simple Room Into a Luxury Room in 3D home redesign animations_stage1'


Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.


74_Turn a Simple Room Into a Luxury Room in 3d Animation shorts.mp4


ic| color: array([255, 255, 255], dtype=uint8)
ic| output_video_path: ('stage1/74_Turn a Simple Room Into a Luxury Room in 3D home redesign '
                        'animations_stage1.mp4')


Processed 1690 frames.
Moviepy - Building video stage2/74_Turn a Simple Room Into a Luxury Room in 3D home redesign animations_stage1.mp4.
MoviePy - Writing audio in 74_Turn a Simple Room Into a Luxury Room in 3D home redesign animations_stage1TEMP_MPY_wvf_snd.mp4


MoviePy - Done.
Moviepy - Writing video stage2/74_Turn a Simple Room Into a Luxury Room in 3D home redesign animations_stage1.mp4



Moviepy - Done !
Moviepy - video ready stage2/74_Turn a Simple Room Into a Luxury Room in 3D home redesign animations_stage1.mp4
Successfully added audio to stage2/74_Turn a Simple Room Into a Luxury Room in 3D home redesign animations_stage1.mp4


In [56]:
import os
from concurrent.futures import ThreadPoolExecutor

def process_file(raw_name):
    v_name = raw_name.split('3d')[0].strip() + ' 3D home redesign animations' + '_stage1'
    filepath = os.path.join('downloads', raw_name)
    print(filepath)  # Assuming ic() was a placeholder for print or logging
    print(v_name)
    mid_frame = get_mid_frame(filepath, output_path='mid_frames/', save_path=True)
    ocr_results = get_ocr_results(mid_frame)
    matches = get_coordinates_for_text(ocr_results, 'stories')
    if matches:
        top_left, bottom_right = matches[0][0], matches[0][2]
        band_color = get_mid_band_color(mid_frame, top_left)
        generate_video(filepath, f'stage1/{v_name}', top_left_coordinate=top_left, bottom_right_coordinate=bottom_right, band_color=band_color)
        add_audio(filepath, f'stage1/{v_name}.mp4', f'stage2/{v_name}.mp4')

def main(filenames_s):
    with ThreadPoolExecutor() as executor:
        # Submit each file to be processed in a separate thread
        for raw_name in reversed(filenames_s):
            executor.submit(process_file, raw_name)

main(filenames_s)


downloads\74_Turn a Simple Room Into a Luxury Room in 3d Animation shorts.mp4
74_Turn a Simple Room Into a Luxury Room in 3D home redesign animations_stage1
downloads\73_Husband Converted Simple Bedroom into Luxury Bedroom In 3d Animation shorts.mp4
73_Husband Converted Simple Bedroom into Luxury Bedroom In 3D home redesign animations_stage1
downloads\72_I Made Luxury & Perfect Bedroom For Son  3D Animation By The Stories Time  shorts.mp4
72_I Made Luxury & Perfect Bedroom For Son  3D Animation By The Stories Time  shorts.mp4 3D home redesign animations_stage1
downloads\71_I Made Luxury & Perfect Bedroom For Daughter  3d Animation By The Stories Time  shorts.mp4
71_I Made Luxury & Perfect Bedroom For Daughter 3D home redesign animations_stage1
downloads\70_I Made Luxury & Perfect Bedroom For Noughty Child  3d Animation By The Stories Time  shorts.mp4
70_I Made Luxury & Perfect Bedroom For Noughty Child 3D home redesign animations_stage1
downloads\69_Turn a Simple Living Room Into a Per

Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.


66_I Made Luxury & Perfect Study Room & Bedroom  3d Animation By The Stories Time  shorts.mp4


Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.
Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.


65_I Made a Luxury & Perfect Bedroom For Two Son  3d Animation By The Stories Time  shorts.mp4
64_I Made a Luxury & Perfect Bathroom For Children  3d Animation By The Stories Time  shorts.mp4
63_Made a Beautiful & Luxury Bedroom For My Son  3d Animation By The Stories Time  shorts.mp4


...

Moviepy - video ready stage2/3_Parents Made a Attractive Bedroom For Twin Daughter 3D home redesign animations_stage1.mp4




t:  63%|██████▎   | 1030/1636 [02:30<00:12, 47.88it/s, now=None]

Successfully added audio to stage2/3_Parents Made a Attractive Bedroom For Twin Daughter 3D home redesign animations_stage1.mp4




t:  63%|██████▎   | 1033/1636 [02:30<00:13, 44.91it/s, now=None]

t:  63%|██████▎   | 1038/1636 [02:30<00:19, 30.47it/s, now=None]

t:  64%|██████▍   | 1045/1636 [02:30<00:16, 36.33it/s, now=None]

t:  64%|██████▍   | 1050/1636 [02:30<00:20, 29.27it/s, now=None]

t:  65%|██████▍   | 1057/1636 [02:31<00:16, 34.12it/s, now=None]

t:  65%|██████▌   | 1064/1636 [02:31<00:14, 39.80it/s, now=None]

t:  66%|██████▌   | 1074/1636 [02:31<00:10, 51.79it/s, now=None]

t:  66%|██████▌   | 1081/1636 [02:31<00:10, 50.90it/s, now=None]

t:  67%|██████▋   | 1089/1636 [02:31<00:09, 56.72it/s, now=None]

t:  67%|██████▋   | 1097/1636 [02:31<00:09, 59.83it/s, now=None]

t:  68%|██████▊   | 1106/1636 [02:31<00:07, 66.35it/s, now=None]

t:  68%|██████▊   | 1114/1636 [02:31<00:07, 65.50it/s, now=None]

t:  69%|██████▊   | 1123/1636 [02:32<00:07, 71.37it/s, now=None]

t:  69%|██████▉   | 1131/1636 [02:32<00:08, 58.10it/s, now=None]

t:  70%|██████▉   | 1139/1636 [02:32<00:08, 55.30it/s, now=None]

t:  70%|

Moviepy - Done !
Moviepy - video ready stage2/0_Parents Made a Perfect & Luxury Bedroom For Daughter 3D home redesign animations_stage1.mp4
Successfully added audio to stage2/0_Parents Made a Perfect & Luxury Bedroom For Daughter 3D home redesign animations_stage1.mp4
